In [45]:
%load_ext autoreload
%autoreload 2
import os
import sys
import numpy as np
import pandas as pd
import xarray as xr
from os.path import join as pjoin
from tqdm.notebook import tqdm
import plotly.graph_objects as go
from scipy.stats import pearsonr, spearmanr, zscore

sys.path.append('/home/austinbaggetta/csstorage3/CircleTrack/CircleTrackAnalysis')
import circletrack_behavior as ctb
import circletrack_neural as ctn
import plotting_functions as pf
import place_cells as pc

xr.set_options(keep_attrs=True)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [46]:
## Settings
dpath = '../../../MultiCon_Imaging/MultiCon_Imaging2/output/'
fig_path = '../../../MultiCon_Imaging/MultiCon_Imaging2/intermediate_figures/'
velocity_thresh = 7
z_thresh = 3
mouse_list = ['mc23', 'mc26']
session_list = [f'A{x}' for x in np.arange(1, 6)] + [f'B{x}' for x in np.arange(1, 6)] + [f'C{x}' for x in np.arange(1, 6)] + [f'D{x}' for x in np.arange(1, 6)]

### Single mouse example.

In [47]:
mouse = 'mc26'
data_type = 'S'
spike_data = xr.open_dataset(pjoin(dpath, f'aligned_minian/{mouse}/{data_type}/{mouse}_{data_type}_7.nc'))[data_type]
x_cm, y_cm = ctb.convert_to_cm(x=spike_data['x'], y=spike_data['y'])
velocity = pc.define_running_epochs(x=x_cm, y=y_cm, t=spike_data['behav_t'])[0]
spike_data = spike_data.assign_coords(x_cm=('frame', x_cm),
                                      y_cm=('frame', y_cm),
                                      velocity=('frame', velocity))
zdata = xr.apply_ufunc(
        zscore,
        spike_data.chunk({'frame': -1, 'unit_id': 50}),
        input_core_dims=[['frame']],
        output_core_dims=[['frame']],
        kwargs={'axis': 1},
        dask='parallelized'
).compute()
mean_activity = zscore(np.mean(zdata, axis=0))

reward_positions = ctb.calculate_reward_positions(spike_data)

/home/austinbaggetta/csstorage3/CircleTrack/CircleTrackAnalysis/place_cells.py:44: RuntimeWarning:

invalid value encountered in divide



In [48]:
mean_activity

<xarray.DataArray 'S' (frame: 35651)>
array([0.5041888 , 0.60724841, 0.46492049, ..., 2.19996654, 2.05203951,
       2.09226076])
Coordinates:
  * frame         (frame) int32 652 653 654 655 656 ... 36299 36300 36301 36302
    behav_t       (frame) float64 0.036 0.06252 0.09452 ... 1.197e+03 1.197e+03
    behav_frame   (frame) int32 1 2 3 4 6 7 ... 51801 51803 51804 51805 51807
    x             (frame) float64 495.0 495.0 495.0 494.0 ... 367.0 369.0 368.0
    y             (frame) float64 315.0 315.0 317.0 319.0 ... 444.0 443.0 443.0
    a_pos         (frame) float64 338.0 338.0 338.0 337.0 ... 289.0 290.0 290.0
    correct_dir   (frame) bool False True False True ... True False True True
    lick_port     (frame) int32 -1 -1 -1 -1 -1 -1 -1 -1 ... -1 -1 -1 -1 -1 -1 -1
    water         (frame) bool False False False False ... False False False
    trials        (frame) float64 0.0 0.0 0.0 0.0 0.0 ... 45.0 45.0 45.0 45.0
    lin_position  (frame) float64 5.899 5.899 5.899 5.882 ... 5.044 5.061 5.061
    probe         (frame) bool False False False False ... False False False
    x_cm          (frame) float64 89.38 89.38 89.38 89.2 ... 66.27 66.63 66.45
    y_cm          (frame) float64 56.88 56.88 57.24 57.6 ... 80.17 79.99 79.99
    velocity      (frame) float64 0.0 0.0 11.28 12.62 ... 22.84 17.56 3.722
Attributes:
    animal:       mc26
    session:      B
    session_two:  B2
    cohort:       mci2
    reward_one:   1
    reward_two:   5
    maze:         maze4
    date:         2023_10_27
    timestamp:    13_17_02
    coordinates:  recording_type animal timestamp unix timestamps session_id ...

In [49]:
fig = pf.custom_graph_template(x_title='Time (s)', y_title='Population Activity (a.u.)', width=1000)
fig.add_trace(go.Scatter(x=mean_activity['behav_t'], y=mean_activity.values, mode='lines', line_color='darkgrey', showlegend=False))
fig.add_trace(go.Scatter(x=mean_activity['behav_t'][mean_activity > z_thresh], y=mean_activity.values[mean_activity.values > z_thresh], 
                         mode='markers', marker_color='red', showlegend=False, marker=dict(size=3)))
fig.add_hline(y=z_thresh, line_width=1, line_dash='dash', line_color='black', opacity=1)
fig.show()

In [50]:
fig = pf.custom_graph_template(x_title='X', y_title='Y')
fig.add_trace(go.Scatter(x=mean_activity['x'][mean_activity.values > z_thresh], 
                         y=mean_activity['y'][mean_activity.values > z_thresh],
                         mode='markers', marker_color='darkgrey', opacity=0.7, showlegend=False))
for pair in reward_positions:
    fig.add_trace(go.Scatter(x=pair[0], y=pair[1], mode='markers', marker_color='black', showlegend=False))
fig.show()

In [51]:
variable_of_interest = 'velocity'
window_size = 60 ## in frames
sampling_rate = 1/30
bursts = mean_activity[mean_activity.values > z_thresh]
size = (window_size * 2) + 1
windowed_data = np.empty((bursts.shape[0], size))
windowed_data.fill(np.nan)
for bur in np.arange(0, bursts.shape[0]-1):
    data = mean_activity[(mean_activity['frame'] >= bursts['frame'][bur] - window_size) & (mean_activity['frame'] <= bursts['frame'][bur] + window_size)]
    if data.shape[0] != size:
        pass
    else:
        if variable_of_interest is not None:
            windowed_data[bur] = data[variable_of_interest]
        else:
            windowed_data[bur] = data

In [61]:
sem = np.nanstd(windowed_data, ddof=1, axis=0) / np.sqrt(windowed_data.shape[0])

array([0.7002454 , 0.6992838 , 0.71352755, 0.71397958, 0.7268982 ,
       0.71238935, 0.73746766, 0.72814709, 0.70054192, 0.69643751,
       0.72373151, 0.76515297, 0.71514415, 0.74527686, 0.73320551,
       0.68299225, 0.69614758, 0.67132316, 0.67933028, 0.65780348,
       0.66748085, 0.6542006 , 0.64488027, 0.66272146, 0.66826863,
       0.69336321, 0.7329279 , 0.74372379, 0.74297514, 0.75178695,
       0.74397186, 0.74574975, 0.74927354, 0.73942066, 0.75368392,
       0.72220796, 0.66569286, 0.67022481, 0.69441417, 0.71972457,
       0.69156048, 0.66986548, 0.67074446, 0.64894975, 0.65447939,
       0.67810749, 0.66767174, 0.66501224, 0.69104287, 0.68982548,
       0.69269232, 0.64383151, 0.6071628 , 0.60555274, 0.62129244,
       0.62392412, 0.58782908, 0.59703206, 0.59821819, 0.54991673,
       0.61004773, 0.56468186, 0.5092878 , 0.50751733, 0.47853118,
       0.54680441, 0.56044879, 0.51946456, 0.52472404, 0.5349831 ,
       0.51810927, 0.51974354, 0.52635221, 0.52789108, 0.54820

In [64]:
avg_activity = np.nanmean(windowed_data, axis=0)
sem = np.nanstd(windowed_data, ddof=1, axis=0) / np.sqrt(windowed_data.shape[0])
x_data = np.arange(-(window_size * sampling_rate), (window_size * sampling_rate)+sampling_rate, sampling_rate)
fig = pf.custom_graph_template(x_title='Time (s)', y_title='Velocity (cm/s)')
fig.add_trace(go.Scatter(x=x_data, y=avg_activity, line_color='midnightblue', showlegend=False))
fig.add_trace(go.Scatter(name='Upper Bound', x=x_data, y=avg_activity + sem, mode='lines',
                                 marker=dict(color='rgba(169,169,169,0.4)'), line=dict(width=0), showlegend=False))
fig.add_trace(go.Scatter(name='Lower Bound', x=x_data, y=avg_activity - sem, marker=dict(color='rgba(169,169,169,0.4)'),
                            line=dict(width=0), mode='lines', fillcolor='rgba(169,169,169,0.4)', fill='tonexty', 
                            showlegend=False))
fig.show()

### One mouse, all that mouse's sessions as subplots.

In [71]:
mouse = 'mc26'
data_type = 'S'
variable_of_interest = 'velocity'
window_size = 60 ## in frames
sampling_rate = 1/30 ## 30fps
size = (window_size * 2) + 1
avg_color = 'midnightblue'
error_color = 'rgba(169,169,169,0.4)'
fig = pf.custom_graph_template(x_title='', y_title='', rows=4, columns=5, shared_y=True,
                               height=1200, width=1200, titles=session_list)
x_data = np.arange(-(window_size * sampling_rate), (window_size * sampling_rate)+sampling_rate, sampling_rate)

mouse_path = pjoin(dpath, f'aligned_minian/{mouse}/{data_type}/')
for idx, session in enumerate(os.listdir(mouse_path)):
        if (mouse == 'mc26') & (idx > 10) & (idx < 17):
                idx += 1
        elif (mouse == 'mc26') & (idx == 17):
                idx += 2
        elif (mouse == 'mc23') & (idx > 14):
                idx += 1

        if idx < 5:
                row, col = 1, idx + 1
        elif (idx >= 5) & (idx < 10):
                row, col = 2, idx - 4
        elif (idx >= 10) & (idx < 15):
                row, col = 3, idx - 9
        else:
                row, col = 4, idx - 14

        spike_data = xr.open_dataset(pjoin(mouse_path, session))[data_type]
        x_cm, y_cm = ctb.convert_to_cm(x=spike_data['x'], y=spike_data['y'])
        velocity = pc.define_running_epochs(x=x_cm, y=y_cm, t=spike_data['behav_t'])[0]
        spike_data = spike_data.assign_coords(x_cm=('frame', x_cm),
                                                y_cm=('frame', y_cm),
                                                velocity=('frame', velocity))
        zdata = xr.apply_ufunc(
                zscore,
                spike_data.chunk({'frame': -1, 'unit_id': 50}),
                input_core_dims=[['frame']],
                output_core_dims=[['frame']],
                kwargs={'axis': 1},
                dask='parallelized'
        ).compute()
        mean_activity = zscore(np.mean(zdata, axis=0))

        windowed_data = np.empty((bursts.shape[0], size))
        windowed_data.fill(np.nan)
        for bur in np.arange(0, bursts.shape[0]-1):
                data = mean_activity[(mean_activity['frame'] >= bursts['frame'][bur] - window_size) & (mean_activity['frame'] <= bursts['frame'][bur] + window_size)]
                if data.shape[0] != size:
                        pass
                else:
                        if variable_of_interest is not None:
                                windowed_data[bur] = data[variable_of_interest]
                        else:
                                windowed_data[bur] = data
        avg_activity = np.nanmean(windowed_data, axis=0)
        sem = np.nanstd(windowed_data, ddof=1, axis=0) / np.sqrt(windowed_data.shape[0])
        fig.add_trace(go.Scatter(x=x_data, y=avg_activity, line_color=avg_color, showlegend=False), row=row, col=col)
        fig.add_trace(go.Scatter(name='Upper Bound', x=x_data, y=avg_activity + sem, mode='lines',
                                        marker=dict(color=error_color), line=dict(width=0), showlegend=False), row=row, col=col)
        fig.add_trace(go.Scatter(name='Lower Bound', x=x_data, y=avg_activity - sem, marker=dict(color=error_color),
                                line=dict(width=0), mode='lines', fillcolor=error_color, fill='tonexty', 
                                showlegend=False), row=row, col=col)
fig.update_yaxes(title='Velocity (cm/s)', col=1)
fig.update_xaxes(title='Time (s)', row=4)
fig.show()

/home/austinbaggetta/csstorage3/CircleTrack/CircleTrackAnalysis/place_cells.py:44: RuntimeWarning:

invalid value encountered in divide

/home/austinbaggetta/csstorage3/CircleTrack/CircleTrackAnalysis/place_cells.py:44: RuntimeWarning:

invalid value encountered in divide

/home/austinbaggetta/csstorage3/CircleTrack/CircleTrackAnalysis/place_cells.py:44: RuntimeWarning:

invalid value encountered in divide

/home/austinbaggetta/csstorage3/CircleTrack/CircleTrackAnalysis/place_cells.py:44: RuntimeWarning:

invalid value encountered in divide

/home/austinbaggetta/csstorage3/CircleTrack/CircleTrackAnalysis/place_cells.py:44: RuntimeWarning:

invalid value encountered in divide

/home/austinbaggetta/csstorage3/CircleTrack/CircleTrackAnalysis/place_cells.py:44: RuntimeWarning:

invalid value encountered in divide

/home/austinbaggetta/csstorage3/CircleTrack/CircleTrackAnalysis/place_cells.py:44: RuntimeWarning:

invalid value encountered in divide

/home/austinbaggetta/csstorage3/CircleTra